### Minimal ensemble code

This code builds a simple bagging ensemble based on Kfold train/val split. Use it for quick idea testing with GPT-5-assisted tree generation.

In [ ]:
# Local dataset settings
DATA_PATH = "mydata/data.csv"
TARGET_COL = "PM2.5"
TASK_TYPE = "regression"  # regression | binary | multiclass
RANDOM_STATE = 42
TEST_SIZE = 0.2
VAL_SIZE = 0.2
N_REPEATS = 1

dataset_name = "pm25_local"
results_path = "data/tree_scores.pm25_local.json"

In [ ]:
import os
import re
import json
import numpy as np
import pandas as pd
import smolagents
from huggingface_hub import login
import proxy_api_model
import prompting
import tree_agent
from sklearn.model_selection import train_test_split
from task import metric_func_by_task

login(token="")
login(token="")
# V-- this uses a GPT-5 model over an API. Replace with https://smolagents.org/docs/agents-guided-tour/
model = proxy_api_model.ProxyAPIModel(
    model_id="deepseek-reasoner",
    api_base="https://api.deepseek.com/v1",  # <-- https://your/openai-like/api/v1/chat/completions
    api_key="sk-50f7e5e092e04da4be8f8f8bb3f6d103",  # <-- use your token
    max_new_tokens=1024 * 8,
    callback=lambda msg, **etc: print(  # print model thoughts before code
        re.sub(r"<code>.*?</code>", "<code omitted>", msg.content, flags=re.DOTALL)
    ),
)

# Load local dataset
if not os.path.exists(DATA_PATH):
    raise FileNotFoundError(f"DATA_PATH not found: {DATA_PATH}")

df = pd.read_csv(DATA_PATH)

if TARGET_COL not in df.columns:
    matches = [c for c in df.columns if c.lower() == TARGET_COL.lower()]
    if matches:
        TARGET_COL = matches[0]
    else:
        raise ValueError(
            f"Target column '{TARGET_COL}' not found in data columns: {list(df.columns)}"
        )

X = df.drop(columns=[TARGET_COL])
y = df[TARGET_COL].to_numpy()

task_type = TASK_TYPE
metric_func = metric_func_by_task[task_type]
metric_name = prompting.metrics_by_task[task_type]

cat_cols = [c for c in X.columns if X[c].dtype == "object"]
num_cols = [c for c in X.columns if c not in cat_cols]

# Dataset description to help the LLM form hypotheses
feature_list = ", ".join(X.columns)
cat_list = ", ".join(cat_cols) if cat_cols else "none"
num_list = ", ".join(num_cols) if num_cols else "none"

dataset_desc = f"""
<dataset>
Your task is to predict PM2.5.
Size: {len(X)} total (full dataset)
Feature columns: {feature_list}
Categorical columns: {cat_list}
Numeric columns: {num_list}
Targets: {TARGET_COL} (float)
Metric: {metric_name}
</dataset>
""".strip()

airfoil_self_noise 1503 363612
anneal 898 363614
Another-Dataset-on-used-Fiat-500 1538 363615
blood-transfusion-service-center 748 363621
concrete_compressive_strength 1030 363625
credit-g 1000 363626
diabetes 768 363629
Fitness_Club 1500 363671
hazelnut-spread-contaminant-detection 2400 363674
healthcare_insurance_expenses 1338 363675
Is-this-a-good-customer 1723 363682
Marketing_Campaign 2240 363684
maternal_health_risk 1014 363685
qsar-biodeg 1054 363696
QSAR_fish_toxicity 907 363698
website_phishing 1353 363707
MIC 1699 363711


In [ ]:
test_scores = []
for repeat_index in range(N_REPEATS):
    print("Beginning repeat", repeat_index)
    split_seed = RANDOM_STATE if N_REPEATS == 1 else RANDOM_STATE + repeat_index

    X_train_full, X_test, y_train_full, y_test = train_test_split(
        X,
        y,
        test_size=TEST_SIZE,
        random_state=split_seed,
        stratify=None if task_type == "regression" else y,
    )
    X_train, X_val, y_train, y_val = train_test_split(
        X_train_full,
        y_train_full,
        test_size=VAL_SIZE,
        random_state=split_seed,
        stratify=None if task_type == "regression" else y_train_full,
    )

    result = tree_agent.TreeAgent(model=model).run(
        task=f"""
Build the optimal decision tree for the '{dataset_name}' dataset.
You are given access to 4 data variables in your python environment:
 - X_train, X_val are pandas dataframes with named feature columns (see below) that may need preprocessing;
 - y_train, y_val are numpy arrays (1d) with targets, also described below;

Dataset description (use it to form hypotheses):
{dataset_desc}

Here's one way you could construct before you begin editing it manually:
{prompting.starter_snippets_by_task[task_type]}

Now begin: view the data variables, preprocess as necessary, train a baseline tree, then propose the first hypothesis and start improving.
Focus on drawing conclusions from data, looking at the tree (e.g. via print) and using your own intuition about the problem for manual tree edits.
Quality is more important than speed: take as many steps as you need to get the best tree.
""".strip(),
        additional_args=dict(
            X_train=X_train.copy(),
            y_train=y_train.copy(),
            X_val=X_val.copy(),
            y_val=y_val.copy(),
        ),
    )

    y_pred_i = result["model"].predict(result["preprocess_features"](X_test.copy()))
    if task_type == "multiclass":  # normalize for logloss
        y_pred_i = y_pred_i / y_pred_i.sum(axis=-1, keepdims=True)
    test_score = metric_func(y_test, y_pred_i)
    print(f"Test {metric_name} score #{repeat_index}: {test_score:.5f}")
    test_scores.append(test_score)
    with open(results_path, "w") as f:
        json.dump(test_scores, f, ensure_ascii=False, indent=2)

Beginning repeat 0
Inferred task type: multiclass


╭──────────────────────────────────────────────────── New run ────────────────────────────────────────────────────╮
│                                                                                                                 │
│ Build the optimal decision tree for the 'anneal' dataset.                                                       │
│ You are given access to 4 data variables in your python environment:                                            │
│  - X_train, X_val are pandas dataframes with named feature columns (see below) that may need preprocessing;     │
│  - y_train, y_val are numpy arrays (1d) with targets, also described below;                                     │
│                                                                                                                 │
│ Dataset description (use it to form hypotheses):                                                                │
│                                                                                                                 │
│ <dataset>                                                                                                       │
│ Your task is to classify the steel annealing condition.                                                         │
│ The dataset contains descriptions of steel production and annealing processes with categorical and continuous   │
│ variables.                                                                                                      │
│                                                                                                                 │
│ Size: 478 total (train and val)                                                                                 │
│                                                                                                                 │
│ Feature descriptions:                                                                                           │
│ - `family`: Categorical. Steel family (GB, GK, GS, TN, ZA, ZF, ZH, ZM, ZS, --).                                 │
│ - `product_type`: Categorical. Product type (C, H, G).                                                          │
│ - `steel`: Categorical. Steel symbol (R, A, U, K, M, S, W, V, --).                                              │
│ - `carbon`: Float. Carbon content.                                                                              │
│ - `hardness`: Float. Hardness value.                                                                            │
│ - `temper_rolling`: Categorical. Temper rolling (T, --).                                                        │
│ - `condition`: Categorical. Condition (S, A, X, --).                                                            │
│ - `formability`: Categorical. Formability rating (1–5, --).                                                     │
│ - `strength`: Float. Strength measurement.                                                                      │
│ - `non_ageing`: Categorical. Non-ageing indicator (N, --).                                                      │
│ - `surface_finish`: Categorical. Surface finish (P, M, --).                                                     │
│ - `surface_quality`: Categorical. Surface quality (D, E, F, G, --).                                             │
│ - `enamelability`: Categorical. Enamelability rating (1–5, --).                                                 │
│ - `bc`, `bf`, `bt`, `bl`, `m`, `cbond`, `marvi`, `exptl`, `ferro`, `corr`, `lustre`, `jurofm`, `s`, `p`:        │
│ Categorical. Various binary quality/chemical indicators (Y, --).                                                │
│ - `bw_me`: Categorical. BW/ME indicator (B, M, --).                                                             │
│ - `chrom`: Categorical. Chromium indicator (C, --).                                                             │
│ - `phos`: Categorical. Phosphorus indicator (P, --).  

━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ Step 1 ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━

Thought: I will inspect the raw data to understand shapes, class balance, feature types, and missing/categorical values. Hypothesis: Many categorical features with "not_applicable" need one-hot encoding; numeric features seem already numeric. I will print basic summaries to guide preprocessing choices and a baseline model setup.

<code omitted>


─ Executing parsed code: ──────────────────────────────────────────────────────────────────────────────────────── 
  import numpy as np                                                                                               
  import pandas as pd                                                                                              
  from collections import Counter                                                                                  
                                                                                                                   
  print("Train shape:", X_train.shape, "Val shape:", X_val.shape)                                                  
  print("Columns:", list(X_train.columns))                                                                         
  print("y_train classes/counts:", Counter(y_train))                                                               
  print("y_val classes/counts:", Counter(y_val))                                                                   
                                                                                                                   
  # Identify categorical vs numeric by dtype and known description                                                 
  cat_cols = [c for c in X_train.columns if X_train[c].dtype == 'object']                                          
  num_cols = [c for c in X_train.columns if c not in cat_cols]                                                     
  print("Categorical columns:", cat_cols)                                                                          
  print("Numeric columns:", num_cols)                                                                              
                                                                                                                   
  # Peek unique values for a few categorical columns                                                               
  for c in cat_cols[:10]:                                                                                          
      print(c, "unique:", X_train[c].nunique(), "sample:", X_train[c].unique()[:6])                                
                                                                                                                   
  # Basic stats for numeric columns                                                                                
  print(X_train[num_cols].describe().T)                                                                            
 ─────────────────────────────────────────────────────────────────────────────────────────────────────────────────

...

Thought:
We have a strong baseline with careful preprocessing (dropping constant features and one-hot encoding categoricals). We then trained a compact tree and iteratively improved it by targeted local grafts where validation loss was concentrated. Specifically, we:
- Grafted a local subtree at node 4 (splitting on strength for surface-quality_not_applicable and hardness<=75 branch), perfectly separating classes 1 and 2 on its validation subset.
- Refined node 5 by splitting on width, improving class-4 vs class-2.
- Refined node 9 (within the condition_S branch) to split on surface-finish_P and strength, carving out classes 0,1,2 appropriately.
Smoothing large confident leaf (node 3) did not help; node 11 had only one validation sample and local refinements did not improve its partial loss, so we left it as-is.

The resulting model achieves a much lower validation log loss.

<code omitted>


─ Executing parsed code: ──────────────────────────────────────────────────────────────────────────────────────── 
  from copy import deepcopy                                                                                        
  import numpy as np                                                                                               
  import pandas as pd                                                                                              
  from pandas.api.types import is_categorical_dtype, is_object_dtype                                               
                                                                                                                   
  # Capture the training feature columns and constant columns discovered during development                        
  feature_columns = list(Xtr.columns)                                                                              
  const_cols_final = ['product-type', 'm', 'marvi', 'corr', 'jurofm', 's', 'p']  # constants across train+val      
                                                                                                                   
  def preprocess_features(X: pd.DataFrame):                                                                        
      Xp = X.copy()                                                                                                
      # Drop known constant columns                                                                                
      drop_cols = [c for c in const_cols_final if c in Xp.columns]                                                 
      if drop_cols:                                                                                                
          Xp = Xp.drop(columns=drop_cols)                                                                          
      # One-hot encode categoricals (category or object dtype)                                                     
      cat_cols_local = [c for c in Xp.columns if is_categorical_dtype(Xp[c]) or is_object_dtype(Xp[c])]            
      Xd = pd.get_dummies(Xp, columns=cat_cols_local, dummy_na=False)                                              
      # Align to training columns: add missing as 0, drop extras, and order                                        
      for c in feature_columns:                                                                                    
          if c not in Xd.columns:                                                                                  
              Xd[c] = 0                                                                                            
      Xd = Xd.reindex(columns=feature_columns, fill_value=0)                                                       
      return Xd                                                                                                    
                                                                                                                   
  # Final artifacts                                                                                                
  final_answer({                                                                                                   
      "summary": "Built a compact, interpretable decision tree for anneal using one-hot encoded categoricals and   
  dropped constants. Starting from a pruned baseline, I targeted high-loss leaves and grafted local subtrees: (1)  
  split node 4 by strength to cleanly separate classes 1 vs 2; (2) split node 5 by width to better distinguish     
  class 4 from class 2; (3) refined node 9 by surface-finish_P and strength to separate classes 0/1/2. Smoothing   
  on the large class-2 leaf did not help and was reverted. The final tree yields strong, calibrated probabilities  
  with low validation log loss.",                                                                                  
      "train_score": best_train_ll,                      

Final answer: {'summary': 'Built a compact, interpretable decision tree for anneal using one-hot encoded 
categoricals and dropped constants. Starting from a pruned baseline, I targeted high-loss leaves and grafted local 
subtrees: (1) split node 4 by strength to cleanly separate classes 1 vs 2; (2) split node 5 by width to better 
distinguish class 4 from class 2; (3) refined node 9 by surface-finish_P and strength to separate classes 0/1/2. 
Smoothing on the large class-2 leaf did not help and was reverted. The final tree yields strong, calibrated 
probabilities with low validation log loss.', 'train_score': 0.031575742207982926, 'val_score': 
0.06980011393983944, 'model':  if surface-quality_not_applicable <= 0.5:  # id: 0, then id: 1, else id: 6, value: 
[0.008, 0.111, 0.762, 0.075, 0.044]
  then: if hardness <= 75:  # id: 1, then id: 2, else id: 5, value: [0, 0.009, 0.931, 0, 0.06]
    then: if strength <= 155:  # id: 2, then id: 3, else id: 4, value: [0, 0.009, 0.988, 0, 0.003]
      then: leaf value=[0, 0, 0.997, 0, 0.003]  # id: 3
      else: if strength <= 550:  # id: 4, then id: 15, else id: 16, value: 0.824
        then: leaf value=[0, 0, 1, 0, 0]  # id: 15
        else: leaf value=[0, 1, 0, 0, 0]  # id: 16
    else: if width <= 109.5:  # id: 5, then id: 17, else id: 18, value: 0.952
      then: leaf value=[0, 0, 0.333, 0, 0.667]  # id: 17
      else: leaf value=[0, 0, 0, 0, 1]  # id: 18
  else: if family_TN <= 0.5:  # id: 6, then id: 7, else id: 14, value: [0.031, 0.388, 0.302, 0.279, 0]
    then: if carbon <= 3:  # id: 7, then id: 8, else id: 13, value: [0.043, 0.538, 0.419, 0, 0]
      then: if condition_S <= 0.5:  # id: 8, then id: 9, else id: 10, value: [0.067, 0.833, 0.1, 0, 0]
        then: if surface-finish_P <= 0.5:  # id: 9, then id: 19, else id: 22, value: [0.333, 0.417, 0.25]
          then: if strength <= 450:  # id: 19, then id: 20, else id: 21, value: [0.571, 0, 0.429]
            then: leaf value=[1, 0, 0, 0, 0]  # id: 20
            else: leaf value=[0, 0, 1, 0, 0]  # id: 21
          else: leaf value=[0, 1, 0, 0, 0]  # id: 22
        else: if steel_R <= 0.5:  # id: 10, then id: 11, else id: 12, value: [0, 0.938, 0.062, 0, 0]
          then: leaf value=[0, 0.727, 0.273, 0, 0]  # id: 11
          else: leaf value=[0, 1, 0, 0, 0]  # id: 12
      else: leaf value=[0, 0, 1, 0, 0]  # id: 13
    else: leaf value=[0, 0, 0, 1, 0]  # id: 14, 'preprocess_features': <function create_function.<locals>.new_func 
at 0x7ff864137420>}

[Step 11: Duration 68.69 seconds| Input tokens: 64,529 | Output tokens: 25,646]

Test Log Loss (sklearn.metrics.log_loss) score #4: 0.14293


In [ ]:
test_scores

[0.08061947848102688,
 0.32442495917804665,
 0.0700032991596908,
 0.07289752745568814,
 0.14292990538497083]

In [ ]:
np.mean(test_scores), np.std(test_scores, ddof=1)

(0.13817503393188466, 0.10831992394475876)